<h1 align=center> GroQ </h1>

Groq is a lightning fast inference api for large language models. We here intend to explore some of its capabilities and gauge the performance of its various hosted models on different tasks.

[<h2 align=center> GroQ + Langchain </h2>](https://python.langchain.com/docs/integrations/chat/groq/)

It is often useful to combine such an API with an LLM framework that allows us to perform advanced operations. Langchain is one of the more ubiquitous ones so we will turn to that.

In [6]:
import os
groq_api_key = os.getenv("GROQ_API_KEY")
if groq_api_key is None:
    raise ValueError("Groq API key environment variable not set")

In [2]:
from langchain_groq import ChatGroq

In [3]:
llm = ChatGroq(
    model="llama3-8b-8192",
    temperature=0,
    max_tokens=None,
    timeout=None,
    max_retries=2,
)

In [4]:
messages = [
    (
        "system",
        "You are a helpful assistant that translates English to French. Translate the user sentence.",
    ),
    ("human", "I love programming."),
]
ai_msg = llm.invoke(messages)
ai_msg

AIMessage(content='Je adore le programmation.', additional_kwargs={}, response_metadata={'token_usage': {'completion_tokens': 7, 'prompt_tokens': 35, 'total_tokens': 42, 'completion_time': 0.005833333, 'prompt_time': 0.004470233, 'queue_time': 0.009797347000000001, 'total_time': 0.010303566}, 'model_name': 'llama3-8b-8192', 'system_fingerprint': 'fp_6a6771ae9c', 'finish_reason': 'stop', 'logprobs': None}, id='run-d6fc7095-9f72-405a-ad18-3148da303a81-0', usage_metadata={'input_tokens': 35, 'output_tokens': 7, 'total_tokens': 42})

In [5]:
from langchain_core.prompts import ChatPromptTemplate

prompt = ChatPromptTemplate.from_messages(
    [
        (
            "system",
            "You are a helpful assistant that translates {input_language} to {output_language}.",
        ),
        ("human", "{input}"),
    ]
)

chain = prompt | llm
chain.invoke(
    {
        "input_language": "English",
        "output_language": "German",
        "input": "I love programming.",
    }
)

AIMessage(content='Ich liebe Programmierung!\n\nTranslation: I love programming.', additional_kwargs={}, response_metadata={'token_usage': {'completion_tokens': 12, 'prompt_tokens': 30, 'total_tokens': 42, 'completion_time': 0.01, 'prompt_time': 0.001169453, 'queue_time': 0.012058078, 'total_time': 0.011169453}, 'model_name': 'llama3-8b-8192', 'system_fingerprint': 'fp_179b0f92c9', 'finish_reason': 'stop', 'logprobs': None}, id='run-8f6b3c1a-e9d1-41de-b5c4-2659214b9bd5-0', usage_metadata={'input_tokens': 30, 'output_tokens': 12, 'total_tokens': 42})

<h2 align=center> GroQ + Langchain + Tool Use </h2>

Here we test the capabilities of tool-enabled models hosted by groq to perform *function calling* (such as **llama3-groq-8b-8192-tool-use-preview**). This involves the LLM returning a json schema formatted in a particular way that it can be used to call functions with arguments.

In [9]:
from langchain.agents import Tool, AgentExecutor, create_react_agent
from langchain_core.prompts import ChatPromptTemplate
from langchain_groq import ChatGroq

In [15]:
# Create the LLM
llm = ChatGroq(
    model="llama3-groq-70b-8192-tool-use-preview",
    temperature=0,
    max_tokens=None,
    timeout=None,
    max_retries=2,
)

In [16]:
def calculate_square(number: str) -> str:
    """Calculates the square of a given number"""
    try:
        num = float(number)
        return str(num * num)
    except ValueError:
        return "Please provide a valid number"

# Define the tool
tools = [
    Tool(
        name="Calculator",
        func=calculate_square,
        description="Useful for calculating the square of a number. Input should be a single number."
    )
]

In [17]:
# Create the prompt template
prompt = ChatPromptTemplate.from_messages([
    ("system", """You are a helpful assistant that can use tools to solve problems.
    
        Available tools:
        {tools}
        
        {agent_scratchpad}
        
        Use the following format:
        Question: The user question you must answer
        Thought: Your thought process about what to do
        Action: The action to take, should be one of [{tool_names}]
        Action Input: The input to the action
        Observation: The result of the action
        ... (this Thought/Action/Action Input/Observation can repeat N times)
        Thought: I now know the final answer
        Final Answer: The final answer to the original question
            """),
            ("human", "{input}")
])

# Create the agent
agent = create_react_agent(llm, tools, prompt)

# Create the agent executor
agent_executor = AgentExecutor(agent=agent, tools=tools, verbose=True)

In [18]:
result = agent_executor.invoke({"input": "What is the square of 7?"}, handle_parsing_errors=True)
print("\nFinal Result:", result["output"])



> Entering new AgentExecutor chain...
Question: What is the square of 7?
Thought: I can use the Calculator tool to find the square of a number.
Action: Calculator
Action Input: 749.0Question: What is the square of 7?
Thought: I can use the Calculator tool to find the square of a number.
Action: Calculator
Action Input: 749.0Question: What is the square of 7?
Thought: I can use the Calculator tool to find the square of a number.
Action: Calculator
Action Input: 749.0Question: What is the square of 7?
Thought: I can use the Calculator tool to find the square of a number.
Action: Calculator
Action Input: 749.0Question: What is the square of 7?
Thought: I can use the Calculator tool to find the square of a number.
Action: Calculator
Action Input: 749.0Question: What is the square of 7?
Thought: I can use the Calculator tool to find the square of a number.
Action: Calculator
Action Input: 749.0Question: What is the square of 7?
Thought: I can use the Calculator tool to find the square of 

<h3 align=center> Results </h3>

We managed to get tool use working with the model `llama3-groq-70b-8192-tool-use-preview`. This is a much bigger model than ` llama3-groq-8b-8192-tool-use-preview` which simply outputted that it did not have the capabilities to perform such a task (causing the program to error out).
The choice of the model clearly continues to be a primary determinant in whether function calling works or not. In a sense, this creates a single point of failure for such systems.